### check names for swedish nature reserves in iNaturalist
* this [Notebook](https://github.com/salgo60/geojsonKML/blob/main/notebook/Find%20iNaturalist%20places.ipynb)
* api [iNaturlist](https://api.inaturalist.org/v1/docs/ )
* [discussion at iNaturlist forum if we can add protected areas missing](https://forum.inaturalist.org/t/all-swedish-nature-reserves-as-places-available/47854/5?u=salgo60)
 
version
* 0.1 use objects with instance [Q179049](https://www.wikidata.org/wiki/Q179049 )
* 0.2 use objects with [P3613](https://www.wikidata.org/wiki/Property:P3613) Naturvårdsregistret ID see [issue #1](https://github.com/salgo60/geojsonKML/issues/1)
* 0.201 added sessions and user agent and limit per_minute = 6, per_day = 100000


 

In [1]:
from datetime import datetime
start_time  = datetime.now()
print("Last run: ", start_time)

Last run:  2024-01-01 18:21:19.033139


In [2]:
from SPARQLWrapper import SPARQLWrapper, JSON 
import sys

from pyinaturalist import *
from pyinaturalist import ClientSession

session = ClientSession(expire_after=timedelta(days=5))
session = ClientSession(user_agent='GITHUB salgo60/geojsonKML')
#pyinaturalist.user_agent = "GIThUB salgo60/geojsonKML"
session = ClientSession( per_minute = 6, per_day = 100000)

endpoint_url = "https://query.wikidata.org/sparql"

query = """#title: Sweden nature reserve - geoshapeRaw for all objects with P3613 Naturvårdsregistret ID
SELECT ?wd ?wdLabel ?inatPid ?inatP  ?geoshapeRaw    WHERE {
   ?wd wdt:P3613 ?Natid
  #  wdt:P131/wdt:P131 wd:Q104231.
  #   wdt:P17 wd:Q34.
  OPTIONAL {?wd wdt:P7471 ?inatPid}
  BIND(URI(CONCAT("https://www.inaturalist.org/places/",?inatPid)) as ?inatP)
  OPTIONAL {?wd wdt:P3896 ?geoshape}
  BIND(URI(CONCAT(REPLACE(REPLACE(str(?geoshape),"data/main/","w/index.php?title="),"\\\\+", "_"),"&action=raw")) AS ?geoshapeRaw)
 
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en,sv". }
}
ORDER BY (?wdLabel)"""


def get_results(endpoint_url, query):
    user_agent = "WDQS-example Python/%s.%s" % (sys.version_info[0], sys.version_info[1])
    # TODO adjust user agent; see https://w.wiki/CX6
    sparql = SPARQLWrapper(endpoint_url, agent=user_agent)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    return sparql.query().convert()


def saveUrlToFile(filename  , url):

    try:
        response = requests.get(url)
        if response.status_code == 200:
            with open(filename, 'wb') as file:
                file.write(response.content)
            print(f"GeoJSON data successfully saved to {filename}")
        else:
            print(f"Failed to fetch data. Status code: {response.status_code}")
    except Exception as e:
        print(f"An error occurred: {str(e)}")
        
def calliNaturalistplace( name ) :
      
    places = get_places_autocomplete(name, session=session )
    for p in places['results']:
        pprint(p)

def printItemLine(wd, name, inatPid):
            
    if inatPid:
       print(wd, name, f" - iNaturalist place ID: {inatPid}")
    else:
       print(wd, name )

def checkPlacesiNaturalist():

    results = get_results(endpoint_url, query)
    for result in results["results"]["bindings"]:
        try:
            name = result["wdLabel"]["value"]      
            inatPid = result.get("inatPid", {}).get("value", "") 
            wd = result["wd"]["value"].replace ("http://www.wikidata.org/entity/","")
            
            printItemLine( wd, name, inatPid )
            calliNaturalistplace(name)
             
                
        except Exception as e:
            print(f"An error occurred in SPARQL: {str(e)}")
    return wd,name


checkPlacesiNaturalist()

 


Q89466453 2003318 Tomten nr 1 Kv Bojen
Q108163866 2003576 Ugnen
Q30166449 Abborravan
Q30171424 Abborrtjärnberget
Q91883304 Abborrtjärnbergshuvudet
Q30179734 Abborrtjärnhuvudena
Q30170522 Abborrtjärnsberg
Q10397880 Abborrträsk nature reserve
Q953092 Abisko National Park  - iNaturalist place ID: 69050
Q10397997 Abisko naturvet. station
Q10398010 Aboda
Q10398166 Abullahagen nature reserve
Q29580025 Adelsö-Sättra nature reserve
Q89974448 Agnmyren
Q19977456 Agnäs
Q16495470 Agön-Kråkön
Q30168084 Ahmakero
Q30160602 Ahmarova
Q30177632 Ahmasaajo
Q10404024 Akkelis fjällurskog
Q30175780 Alajaure
Q30201739 Albertas myr
Q2640142 Albrunna lund
Q10404424 Alby nature reserve
Q30176609 Alderängarna
Q16496165 Alebäckakärret
Q16496167 Alebäckasjön
Q16496181 Alenäs


 ID       Latitude    Longitude   Name                            Category   URL                                  
 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 
  157544     31.7474     35.1611   Alena Kacal Yard Squad Circle              https://www.inaturalist.org/places… 

Q30171033 Alkärret
Q30178908 Alkärret i Haboljung
Q10405560 Allarps bjär
Q22063538 Allejaure
Q30163349 Allerums mosse
Q10405618 Allgunnen
Q10405651 Allkvie änge
Q16496360 Almeberget nature reserve
Q19977461 Almö


 ID      Latitude    Longitude   Name        Category   URL                                       
 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 
  31034     14.8063    -91.4845   Almolonga              https://www.inaturalist.org/places/31034 

 ID      Latitude    Longitude   Name                     Category   URL                                       
 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 
  37016     18.8330    -99.8668   Almoloya de Alquisiras              https://www.inaturalist.org/places/37016 

...

 ID      Latitude    Longitude   Name    Category   URL                                       
 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 
  34701     36.0193    138.9322   Ogano              https://www.inaturalist.org/places/34701 

 ID       Latitude    Longitude   Name                      Category   URL                                        
 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 
  100560     -3.9898    104.6267   Ogan Komering Ulu Timur              https://www.inaturalist.org/places/100560 

 ID      Latitude    Longitude   Name                 Category   URL                                       
 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 
  49359     -3.3574    105.4300   Ogan Komering Ilir              https://www.inaturalist.org/places/49359 

Q86968356 Ögonkällan
Q55693535 Öjersbyn
Q55693211 Öjsberget
Q86920863 Ön Lilla Torshälla, 1 hängbjörk m.m.
Q86968657 Ön Tärnehall i Bolmen
Q86968481 Ön Österåsholmen
Q86920850 Önnesmark
Q86918816 Önum
Q86919594 Önum
Q55693532 Örby hagar
Q30174109 Örefjärden-Snöanskärgården
Q86920334 Öresten 6:11 och Surteby-Skallared 2:2 (Navåsen) Kommunalt
Q90210238 Örsbäcks naturreservat
Q55693662 Örtjärnsskogen
Q86920871 Ösby 1:1
Q89123633 Ösbyskogen
Q89552463 Ösjöskogens naturreservat
Q86919940 Östbjörke 1:16
Q55693507 Österslumpen
Q86919597 Österäng Forshem
Q86920750 Östorp 1:5
Q55693461 Östra Ejaröd
Q55692884 Östra Flymen
Q89841077 Östringby naturreservat
Q86920716 Överfors 1:8
Q86919131 Överfors 2:2
Q55619300 Öxared


('Q55619300', 'Öxared')

In [3]:
end = datetime.now()
print("Ended: ", end) 
print('Time elapsed (hh:mm:ss.ms) {}'.format(datetime.now() - start_time))
 

Ended:  2024-01-02 11:46:39.577430
Time elapsed (hh:mm:ss.ms) 17:25:20.544401
